In [1]:
import plotly.express as px
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import seaborn as sns

import re
import random
import nltk
from scipy import sparse
from scipy.sparse import csr_matrix, vstack
from textblob import TextBlob
import pickle
from datetime import datetime

from sklearn.feature_extraction.text import TfidfTransformer, CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score, confusion_matrix
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
import time 
import glob
import requests
import nltk
from langdetect import detect_langs
import pandas as pd
import numpy as np
#for text pre-processing
import re, string
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import SnowballStemmer
from nltk.corpus import wordnet
from nltk.stem import WordNetLemmatizer
nltk.download('punkt')
nltk.download('averaged_perceptron_tagger')
nltk.download('wordnet')
#for model-building
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import classification_report, f1_score, accuracy_score, confusion_matrix
from sklearn.metrics import roc_curve, auc, roc_auc_score
# bag of words
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer
#for word embedding
import gensim
from gensim.models import Word2Vec

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\User\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\User\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\User\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [3]:
import sys
sys.path.append('../Data preprocessing')  # Add the folder to the Python module search path
import simple_feature_engineering as sf

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\User\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [6]:
df=pd.read_csv("../Datasets/FinalData1.csv")

In [7]:
df=df.dropna()

In [8]:
df_unnested = df.assign(Translated_Lyrics=df['Translated_Lyrics'].str.split('\n')).explode('Translated_Lyrics')

In [9]:
df_unnested = df_unnested[df_unnested['Translated_Lyrics'] != '\r']
df_unnested.head()

Artist         Song  \
0  ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  ԱՀԱ ԵՎ ՎԵՐՋ   
0  ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  ԱՀԱ ԵՎ ՎԵՐՋ   
0  ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  ԱՀԱ ԵՎ ՎԵՐՋ   
0  ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  ԱՀԱ ԵՎ ՎԵՐՋ   
0  ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  ԱՀԱ ԵՎ ՎԵՐՋ   

                                              Lyrics  \
0  \r\n\tԱհա և վերջ\n\r\n\tՎերջ հարաժամ և հարատև\...   
0  \r\n\tԱհա և վերջ\n\r\n\tՎերջ հարաժամ և հարատև\...   
0  \r\n\tԱհա և վերջ\n\r\n\tՎերջ հարաժամ և հարատև\...   
0  \r\n\tԱհա և վերջ\n\r\n\tՎերջ հարաժամ և հարատև\...   
0  \r\n\tԱհա և վերջ\n\r\n\tՎերջ հարաժամ և հարատև\...   

               Translated_Lyrics  
0                 Here is an end  
0  End of paragraphs and lasting  
0          As a last closed page  
0          And no return already  
0                 Oh native bugs

In [10]:
import nltk
from nltk.corpus import stopwords

def preprocess_lyrics(df, column_name):
    # Check if the column exists in the DataFrame
    if column_name not in df.columns:
        raise ValueError(f"Column '{column_name}' does not exist in the DataFrame.")

    # Lowercase the lyrics
    df[column_name] = df[column_name].str.lower()

    # Remove stop words
    stop_words = set(stopwords.words('english'))
    df[column_name] = df[column_name].apply(lambda x: ' '.join([word for word in nltk.word_tokenize(x) if word not in stop_words]))

    return df


In [11]:
f_unnested = preprocess_lyrics(df_unnested, 'Translated_Lyrics')
df_unnested[['Artist','Translated_Lyrics']]

Artist               Translated_Lyrics
0    ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ                             end
0    ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ          end paragraphs lasting
0    ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ                last closed page
0    ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ                  return already
0    ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ                  oh native bugs
..              ...                             ...
542    Mi Qani Hogi               let 's lie please
542    Mi Qani Hogi                                
542    Mi Qani Hogi  n't love love believe sky kind
542    Mi Qani Hogi                                
542    Mi Qani Hogi       believe come bar win evil

[18110 rows x 2 columns]

In [12]:
df_unnested = df_unnested.reset_index(drop=True)
df_unnested

Artist         Song  \
0      ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  ԱՀԱ ԵՎ ՎԵՐՋ   
1      ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  ԱՀԱ ԵՎ ՎԵՐՋ   
2      ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  ԱՀԱ ԵՎ ՎԵՐՋ   
3      ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  ԱՀԱ ԵՎ ՎԵՐՋ   
4      ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  ԱՀԱ ԵՎ ՎԵՐՋ   
...               ...          ...   
18105    Mi Qani Hogi  Lav Jamanak   
18106    Mi Qani Hogi  Lav Jamanak   
18107    Mi Qani Hogi  Lav Jamanak   
18108    Mi Qani Hogi  Lav Jamanak   
18109    Mi Qani Hogi  Lav Jamanak   

                                                  Lyrics  \
0      \r\n\tԱհա և վերջ\n\r\n\tՎերջ հարաժամ և հարատև\...   
1      \r\n\tԱհա և վերջ\n\r\n\tՎերջ հարաժամ և հարատև\...   
2      \r\n\tԱհա և վերջ\n\r\n\tՎերջ հարաժամ և հարատև\...   
3      \r\n\tԱհա և վերջ\n\r\n\tՎերջ հարաժամ և հարատև\...   
4      \r\n\tԱհա և վերջ\n\r\n\tՎերջ հարաժամ և հարատև\...   
...                                                  ...   
18105  \n\n\n\n\nԹարմացրու քեզ դու իմացի բախտը քո կող...   
18106  \n\n\n\n\nԹարմացրու քեզ դու իմացի բախտը քո կող...   
18107  \n\n\n\n\nԹարմացրու քեզ դու իմացի բախտը քո կող...   
18108  \n\n\n\n\nԹարմացրու քեզ դու իմացի բախտը քո կող...   
18109  \n\n\n\n\nԹարմացրու քեզ դու իմացի բախտը քո կող...   

                    Translated_Lyrics  
0                                 end  
1              end paragraphs lasting  
2                    last closed page  
3                      return already  
4                      oh native bugs  
...                               ...  
18105               let 's lie please  
18106                                  
18107  n't love love believe sky kind  
18108                                  
18109       believe come bar win evil  

[18110 rows x 4 columns]

In [13]:
# Count vectorization of text
from sklearn.feature_extraction.text import CountVectorizer

# Ticket Data
corpus = df_unnested['Translated_Lyrics'].values

# Creating the vectorizer
vectorizer = CountVectorizer(stop_words='english')

# Converting the text to numeric data
X = vectorizer.fit_transform(corpus)


# Preparing Data frame For machine learning
# Priority column acts as a target variable and other columns as predictors
CountVectorizedData=pd.DataFrame(X.toarray(), columns=vectorizer.get_feature_names())
CountVectorizedData['Priority']=df_unnested['Artist']
print(CountVectorizedData.shape)
CountVectorizedData.head()

(18110, 6971)


C:\Users\User\anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


aa  abandoned  abar  abarthrishev  abbreviation  abdominal  abdomins  able  \
0   0          0     0             0             0          0         0     0   
1   0          0     0             0             0          0         0     0   
2   0          0     0             0             0          0         0     0   
3   0          0     0             0             0          0         0     0   
4   0          0     0             0             0          0         0     0   

   abling  abnorm  ...  zilch  zim  zinart  zircut  zogid  zoma  zombie  zulo  \
0       0       0  ...      0    0       0       0      0     0       0     0   
1       0       0  ...      0    0       0       0      0     0       0     0   
2       0       0  ...      0    0       0       0      0     0       0     0   
3       0       0  ...      0    0       0       0      0     0       0     0   
4       0       0  ...      0    0       0       0      0     0       0     0   

   zurna        Priority  
0      0  ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  
1      0  ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  
2      0  ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  
3      0  ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  
4      0  ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  

[5 rows x 6971 columns]

In [14]:
import gensim
#Loading the word vectors from Google trained word2Vec model
GoogleModel = gensim.models.KeyedVectors.load_word2vec_format('C:/Users/User/Downloads/GoogleNews-vectors-negative300.bin.gz', binary=True,)

In [15]:
WordsVocab=CountVectorizedData.columns[:-1]

# Printing sample words
WordsVocab[0:10]

Index(['aa', 'abandoned', 'abar', 'abarthrishev', 'abbreviation', 'abdominal',
       'abdomins', 'able', 'abling', 'abnorm'],
      dtype='object')

In [16]:
# Defining a function which takes text input and returns one vector for each sentence
def FunctionText2Vec(inpTextData):
    # Converting the text to numeric data
    X = vectorizer.transform(inpTextData)
    CountVecData=pd.DataFrame(X.toarray(), columns=vectorizer.get_feature_names())
    
    # Creating empty dataframe to hold sentences
    W2Vec_Data=pd.DataFrame()
    
    # Looping through each row for the data
    for i in range(CountVecData.shape[0]):

        # initiating a sentence with all zeros
        Sentence = np.zeros(300)

        # Looping thru each word in the sentence and if its present in 
        # the Word2Vec model then storing its vector
        for word in WordsVocab[CountVecData.iloc[i , :]>=1]:
            #print(word)
            if word in GoogleModel.key_to_index.keys():    
                Sentence=Sentence+GoogleModel[word]
        # Appending the sentence to the dataframe
        W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
    return(W2Vec_Data)

In [17]:
# Since there are so many words... This will take some time :( 
# Calling the function to convert all the text data to Word2Vec Vectors
W2Vec_Data=FunctionText2Vec(df_unnested['Translated_Lyrics'])
 
# Checking the new representation for sentences
W2Vec_Data.shape

C:\Users\User\anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W

C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd

C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd

C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd

C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd

...

C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd

C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd

C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd

C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd

(18110, 300)

In [18]:
CountVectorizedData.shape

(18110, 6971)

In [19]:
# Adding the target variable
W2Vec_Data.reset_index(inplace=True, drop=True)
W2Vec_Data['Priority']=CountVectorizedData['Priority']
 
# Assigning to DataForML variable
DataForML=W2Vec_Data
DataForML.head()

0         1         2         3         4         5         6  \
0 -0.040527  0.036133 -0.074219  0.300781 -0.065918 -0.102539  0.013123   
1 -0.097412  0.478516 -0.011963  0.587402 -0.376953 -0.268280  0.533630   
2  0.135742  0.046021  0.225159 -0.089844 -0.093201 -0.086670 -0.226929   
3  0.051270  0.125977 -0.137695  0.088379 -0.085938  0.083984 -0.083496   
4  0.256836  0.401855 -0.082275  0.163574 -0.418945  0.315552 -0.217056   

          7         8         9  ...       291       292       293       294  \
0 -0.142578  0.287109  0.063965  ...  0.148438 -0.170898  0.135742  0.026855   
1 -0.371094  0.615234  0.359863  ... -0.089844 -0.216431  0.009766  0.013184   
2  0.043945  0.805664 -0.112305  ... -0.096191 -0.544922  0.366699  0.018799   
3 -0.414062  0.238281  0.050781  ...  0.156250  0.067871  0.001572  0.125000   
4 -0.027100 -0.089355  0.843750  ... -0.021729 -0.290771 -0.150502 -0.090820   

        295       296       297       298       299        Priority  
0  0.055176 -0.172852 -0.009705  0.012207 -0.128906  ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  
1 -0.106934 -0.299805 -0.211365 -0.053711  0.002625  ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  
2 -0.189697  0.178955 -0.323730 -0.044434 -0.143066  ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  
3  0.075195  0.082520 -0.287109  0.125000 -0.204102  ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  
4 -0.101807 -0.153946 -0.532715  0.237793  0.022034  ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ  

[5 rows x 301 columns]

In [31]:
# Separate Target Variable and Predictor Variables
TargetVariable=DataForML.columns[-1]
Predictors=DataForML.columns[:-1]

X=DataForML[Predictors].values
y=DataForML[TargetVariable].values
from sklearn.preprocessing import StandardScaler, MinMaxScaler
# Choose either standardization or Normalization
# On this data Min Max Normalization is used because we need to fit Naive Bayes

# Choose between standardization and MinMAx normalization
#PredictorScaler=StandardScaler()
PredictorScaler=MinMaxScaler()

# Storing the fit object for later reference
PredictorScalerFit=PredictorScaler.fit(X)
X=PredictorScalerFit.transform(X)

# Split the data into training and testing set
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=428)
PredictorScalerFit=PredictorScaler.fit(X)

# Sanity check for the sampled data
print(X_train.shape)
print(y_train.shape)
print(X_test.shape)
print(y_test.shape)

(14488, 300)
(14488,)
(3622, 300)
(3622,)


In [21]:
# Logistic Regression
from sklearn.linear_model import LogisticRegression
# choose parameter Penalty='l1' or C=1
# choose different values for solver 'newton-cg', 'lbfgs', 'liblinear', 'sag', 'saga'
clf = LogisticRegression(C=10,penalty='l2', solver='newton-cg')

# Printing all the parameters of logistic regression
# print(clf)

# Creating the model on Training Data
LOG=clf.fit(X_train,y_train)

# Generating predictions on testing data
prediction=LOG.predict(X_test)


# Measuring accuracy on Testing Data
from sklearn import metrics
print(metrics.classification_report(y_test, prediction))
#print(metrics.confusion_matrix(y_test,prediction))

## Printing the Overall Accuracy of the model
F1_Score=metrics.f1_score(y_test, prediction, average='weighted')
print('Accuracy of the model on Testing Sample Data:', round(F1_Score,2))

## Importing cross validation function from sklearn
#from sklearn.model_selection import cross_val_score

## Running 10-Fold Cross validation on a given algorithm
## Passing full data X and y because the K-fold will split the data and automatically choose train/test
#Accuracy_Values=cross_val_score(LOG, X , y, cv=10, scoring='f1_weighted')
#print('\nAccuracy values for 10-fold Cross Validation:\n',Accuracy_Values)
#print('\nFinal Average Accuracy of the model:', round(Accuracy_Values.mean(),2))

                    precision    recall  f1-score   support

           Lav Eli       0.36      0.17      0.23        60
          Aram MP3       0.38      0.27      0.32       153
             Arame       0.26      0.20      0.22        56
    Arsen Safaryan       0.21      0.12      0.15       125
           Empyray       0.30      0.33      0.32        51
          HT Hayko       0.33      0.25      0.28       217
Harout Pamboukjian       0.32      0.21      0.25       164
      Mi Qani Hogi       0.10      0.03      0.05       175
             Misho       0.23      0.70      0.35       302
      Razmik Amyan       0.17      0.11      0.13       110
    Silva Hakobyan       0.21      0.15      0.17       109
    ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ       0.31      0.26      0.28       360
             Անդրե       0.08      0.06      0.07        72
Լիլիթ Հովհաննիսյան       0.26      0.18      0.21       205
           ԿՈՄԻՏԱՍ       0.40      0.33      0.36       303
     Հայկ Հակոբյան       0.22      0.13

In [22]:
from sklearn import svm
svm=svm.SVC(C=10,kernel='linear')

In [23]:
LOG1=svm.fit(X_train,y_train)

# Generating predictions on testing data
prediction=LOG1.predict(X_test)


# Measuring accuracy on Testing Data
from sklearn import metrics
print(metrics.classification_report(y_test, prediction))
#print(metrics.confusion_matrix(y_test,prediction))

## Printing the Overall Accuracy of the model
F1_Score=metrics.f1_score(y_test, prediction, average='weighted')
print('Accuracy of the model on Testing Sample Data:', round(F1_Score,2))

                    precision    recall  f1-score   support

           Lav Eli       0.31      0.28      0.30        60
          Aram MP3       0.51      0.55      0.53       153
             Arame       0.34      0.45      0.38        56
    Arsen Safaryan       0.29      0.18      0.23       125
           Empyray       0.34      0.45      0.39        51
          HT Hayko       0.35      0.28      0.31       217
Harout Pamboukjian       0.40      0.31      0.35       164
      Mi Qani Hogi       0.25      0.10      0.14       175
             Misho       0.24      0.70      0.36       302
      Razmik Amyan       0.36      0.26      0.31       110
    Silva Hakobyan       0.38      0.30      0.34       109
    ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ       0.36      0.34      0.35       360
             Անդրե       0.29      0.28      0.28        72
Լիլիթ Հովհաննիսյան       0.40      0.36      0.38       205
           ԿՈՄԻՏԱՍ       0.52      0.35      0.42       303
     Հայկ Հակոբյան       0.33      0.16

In [24]:
from sklearn.ensemble import AdaBoostClassifier
from sklearn.datasets import make_classification

clf = AdaBoostClassifier(n_estimators=300, random_state=0)
LOG2=clf.fit(X_train, y_train)
prediction=LOG2.predict(X_test)
print(metrics.classification_report(y_test, prediction))
#print(metrics.confusion_matrix(y_test,prediction))

## Printing the Overall Accuracy of the model
F1_Score=metrics.f1_score(y_test, prediction, average='weighted')
print('Accuracy of the model on Testing Sample Data:', round(F1_Score,2))

                    precision    recall  f1-score   support

           Lav Eli       0.09      0.03      0.05        60
          Aram MP3       0.14      0.08      0.10       153
             Arame       0.08      0.05      0.06        56
    Arsen Safaryan       0.09      0.05      0.06       125
           Empyray       0.10      0.06      0.07        51
          HT Hayko       0.13      0.09      0.11       217
Harout Pamboukjian       0.09      0.05      0.07       164
      Mi Qani Hogi       0.04      0.01      0.01       175
             Misho       0.22      0.61      0.32       302
      Razmik Amyan       0.06      0.03      0.04       110
    Silva Hakobyan       0.02      0.01      0.01       109
    ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ       0.18      0.20      0.19       360
             Անդրե       0.04      0.01      0.02        72
Լիլիթ Հովհաննիսյան       0.19      0.09      0.13       205
           ԿՈՄԻՏԱՍ       0.21      0.16      0.18       303
     Հայկ Հակոբյան       0.15      0.05

In [25]:
import pickle

# Assuming you have a trained model named 'model'
# Save the model to a file
filename = 'model.pkl'
with open(filename, 'wb') as file:
    pickle.dump(LOG2, file)


In [26]:
# Load the saved model from file
with open(filename, 'rb') as file:
    loaded_model = pickle.load(file)


In [27]:
import pandas as pd
from langdetect import detect_langs

from translate import Translator

def translate_lyrics_list(lines):
    translator = Translator(from_lang='hy', to_lang='en')
    translated_lines = []

    for line in lines:
        translated_line = translator.translate(line)
        translated_lines.append(translated_line)

    return translated_lines

def preprocess_lyrics_list(lines):
    # Lowercase the lyric lines
    lines_lower = [line.lower() for line in lines]

    # Remove stop words
    stop_words = set(stopwords.words('english'))
    lines_filtered = [' '.join([word for word in nltk.word_tokenize(line) if word not in stop_words]) for line in lines_lower]

    return lines_filtered



# Defining a function which converts words into numeric vectors for prediction
def FunctionPredictArtist(inpText):
    
    inpText = translate_lyrics_list(inpText)
    print(translate_lyrics_list(inpText))
    #inpText = preprocess_lyrics_list(inpText)
    #print(translation)
    # Generating the Glove word vector embeddings
    X=FunctionText2Vec(inpText)
    #print(X)
    
    # If standardization/normalization was done on training
    # then the above X must also be converted to same platform
    # Generating the normalized values of X
    X=PredictorScalerFit.transform(X)
    
    # Generating the prediction using Naive Bayes model and returning
    Prediction=loaded_model.predict(X)
    Result=pd.DataFrame(data=inpText, columns=['Translated_Lyrics'])
    Result['Prediction']=Prediction
    return(Result)

In [28]:
example=["Մարդիկ ասում են որ մենակությունից վատ բան չկա էս կյանքում Երբ որ մարդ իրան մենակա զգում Բայց իմ կարծիքով մենակ լնելը ու զգալը Պետչի շփոթել էտի լրիվ տարբեր բաներ են", 
         "Որտև մարդ կա ընգեր չունի կնիկ չունի",
         "Ուրիշների կարծիքով ինքը խեղճա ինքը մեղկա Բայց էտ մարդը իրան լավա զգում իրան տենց դզումա",
         "Լավագույն տղերքը հեռանում են Օտար ափերում բախտ որոնում" ,"Սիրելի կանայք թողնում գնում են Ուրիշների մեջ են մեզ փնտրում",
         "Սովորելով մեկա անգրագետ են մնում Դե բա էտ են կոչում ինքնաճանաչում Ինքնասիրություննա ձեր վրա հաչում չեք է ամաչում Ձեր տնգած բույսը փդում չի էլ կանաչում Ովա ձեզ պաչում պուտանկից բացի գնա քեզ հեքիաթնա կանչում Օրինակ ինձ ցույց տու բնօրինակդ ակնհայտա դու հորինած ես"]

In [29]:
print(example[0])

Մարդիկ ասում են որ մենակությունից վատ բան չկա էս կյանքում Երբ որ մարդ իրան մենակա զգում Բայց իմ կարծիքով մենակ լնելը ու զգալը Պետչի շփոթել էտի լրիվ տարբեր բաներ են


In [32]:
FunctionPredictArtist(example)

['People say that there is nothing wrong with my life when I feel alone, but in my opinion, being alone and feeling alone are completely different things.', "Where there's a man, there's a mage, there's a seal.", "Some people think it's a bad idea, but some people think it's a good idea to feel bad about themselves.", 'The best way to get away from the bad guys is to go on a cruise.', "We're looking for women who are willing to let go of us.", "Learn to be an uneducated person Well, they call you self-awareness Self-awareness doesn't bark at you Don't be ashamed of the plant you planted Doesn't sprout green Don't bark at anyone other than a pout Go to a fairy tale call to yourself For example, show me the original you obviously invented"]


C:\Users\User\anaconda3\lib\site-packages\sklearn\utils\deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W2Vec_Data=W2Vec_Data.append(pd.DataFrame([Sentence]))
C:\Users\User\AppData\Local\Temp\ipykernel_7488\3706690410.py:23: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  W

Translated_Lyrics         Prediction
0  People say that there is nothing wrong with my...  ՌՈՒԲԵՆ ՀԱԽՎԵՐԴՅԱՆ
1  Where there's a man, there's a mage, there's a...     ԱՐԹՈՒՐ ՄԵՍՉՅԱՆ
2  Some people think it's a bad idea, but some pe...              Misho
3  The best way to get away from the bad guys is ...              Misho
4  We're looking for women who are willing to let...              Misho
5  Learn to be an uneducated person Well, they ca...           HT Hayko